<h1><center>Week 3 Session 2</center></h1>

This first cell must be run in order for the programs to run.

In [2]:
#! /usr/bin/env python
from Bio import SeqIO
import gzip
import re
import os


<h3>Task 1: Read a Genebank formatted file</h3>

In [4]:
def readSequences():
    
    #Use rsync to bring the genebank file from NCBI
    os.system('rsync -avzL rsync://rsync.ncbi.nlm.nih.gov/genomes/all/GCF/000/005/845/GCF_000005845.2_ASM584v2/GCF_000005845.2_ASM584v2_genomic.gbff.gz .')

    #Without uncompressing the file, read the file
    with gzip.open('GCF_000005845.2_ASM584v2_genomic.gbff.gz','rt') as f:


        for seq_record in SeqIO.parse(f,"genbank"):
            id = seq_record.id
            feat = seq_record.features
            iterateData(feat)
            
            
def iterateData(features):
    
    #print headers
    print('Accession\tTax ID\tStart\tStop\tStrand\tGene Name\tLocus Tag\tSynonyms\tProtein Name\tEC-number(s)\t'
            +'External References')
    
    #initialze all values
    taxon = ''
    data = []
    for i in features:
        
        #print(i.type)
        if i.type == 'source':
            taxon = readSource(i)

        if i.type == 'CDS':
            
            #print(i)
            #print(type(i.location))
            protein_id,data = readCDS(i)
            print('{}\t{}\t{}'.format(protein_id,taxon,'\t'.join(data)))
        

def readSource(source):
    
    return re.match(r'taxon:([0-9]+)',source.qualifiers['db_xref'][0])[1]
    
def readCDS(cds):
    
    # Initialize the variables to hold the values
    protein_id=''
    gene=''
    products=''
    
    try:
        protein_id = ','.join(cds.qualifiers['protein_id'])
    except KeyError:
        protein_id = 'pseudo'
        
    try:
        gene = ','.join(cds.qualifiers['gene'])
    except KeyError:
        gene = '-'
    
    loc = cds.location
    
    location = re.search(r'\[([0-9]+):([0-9]+)\]\((.)\)',str(loc))
    
    start = location[1]
    stop = location[2]
    strand = location[3]
    
    locus = ','.join(cds.qualifiers['locus_tag'])
    
    synonyms = ','.join(cds.qualifiers['gene_synonym'])
    
    try:
        products = ','.join(cds.qualifiers['product'])
    except KeyError:
        pass
    
    return protein_id,[start,stop,strand,gene,locus,synonyms,products]
    
if __name__ == "__main__":

    readSequences()

Accession	Tax ID	Start	Stop	Strand	Gene Name	Locus Tag	Synonyms	Protein Name	EC-number(s)	External References
NP_414542.1	511145	189	255	+	thrL	b0001	ECK0001; JW4367	thr operon leader peptide
NP_414543.1	511145	336	2799	+	thrA	b0002	ECK0002; Hs; JW0001; thrA1; thrA2; thrD	Bifunctional aspartokinase/homoserine dehydrogenase 1
NP_414544.1	511145	2800	3733	+	thrB	b0003	ECK0003; JW0002	homoserine kinase
NP_414545.1	511145	3733	5020	+	thrC	b0004	ECK0004; JW0003	L-threonine synthase
NP_414546.1	511145	5233	5530	+	yaaX	b0005	ECK0005; JW0004	DUF2502 family putative periplasmic protein
NP_414547.1	511145	5682	6459	-	yaaA	b0006	ECK0006; JW0005	peroxide resistance protein, lowers intracellular iron
NP_414548.1	511145	6528	7959	-	yaaJ	b0007	ECK0007; JW0006	putative transporter
NP_414549.1	511145	8237	9191	+	talB	b0008	ECK0008; JW0007; yaaK	transaldolase B
NP_414550.1	511145	9305	9893	+	mog	b0009	bisD; chlG; ECK0009; JW0008; mogA; yaaG	molybdochelatase incorporating molybdenum into molybdopterin
NP

<h3>Task 2: Use biopython to parsed a FASTA file</h3>

In [5]:
def parse_fasta():
    
    os.system('rsync -avzL rsync://rsync.ncbi.nlm.nih.gov/genomes/all/GCF/000/005/845/GCF_000005845.2_ASM584v2/GCF_000005845.2_ASM584v2_protein.faa.gz .')
    
    with gzip.open('GCF_000005845.2_ASM584v2_protein.faa.gz','rt') as f:
        
        #Print header
        print('Accession\tSequence')
        
        for seq_record in SeqIO.parse(f,'fasta'):
            
            print('{}\t{}'.format(seq_record.id,seq_record.seq))

if __name__ == '__main__':
    
    parse_fasta()

Accession	Sequence
NP_414542.1	MKRISTTITTTITITTGNGAG
NP_414543.1	MRVLKFGGTSVANAERFLRVADILESNARQGQVATVLSAPAKITNHLVAMIEKTISGQDALPNISDAERIFAELLTGLAAAQPGFPLAQLKTFVDQEFAQIKHVLHGISLLGQCPDSINAALICRGEKMSIAIMAGVLEARGHNVTVIDPVEKLLAVGHYLESTVDIAESTRRIAASRIPADHMVLMAGFTAGNEKGELVVLGRNGSDYSAAVLAACLRADCCEIWTDVDGVYTCDPRQVPDARLLKSMSYQEAMELSYFGAKVLHPRTITPIAQFQIPCLIKNTGNPQAPGTLIGASRDEDELPVKGISNLNNMAMFSVSGPGMKGMVGMAARVFAAMSRARISVVLITQSSSEYSISFCVPQSDCVRAERAMQEEFYLELKEGLLEPLAVTERLAIISVVGDGMRTLRGISAKFFAALARANINIVAIAQGSSERSISVVVNNDDATTGVRVTHQMLFNTDQVIEVFVIGVGGVGGALLEQLKRQQSWLKNKHIDLRVCGVANSKALLTNVHGLNLENWQEELAQAKEPFNLGRLIRLVKEYHLLNPVIVDCTSSQAVADQYADFLREGFHVVTPNKKANTSSMDYYHQLRYAAEKSRRKFLYDTNVGAGLPVIENLQNLLNAGDELMKFSGILSGSLSYIFGKLDEGMSFSEATTLAREMGYTEPDPRDDLSGMDVARKLLILARETGRELELADIEIEPVLPAEFNAEGDVAAFMANLSQLDDLFAARVAKARDEGKVLRYVGNIDEDGVCRVKIAEVDGNDPLFKVKNGENALAFYSHYYQPLPLVLRGYGAGNDVTAAGVFADLLRTLSWKLGV
NP_414544.1	MVKVYAPASSANMSVGFDVLGAAVTPVDGALLGDVVTVEAAETFSLNNLGRFADKLPSEPRENIVYQCWERFCQELGKQIPVAMTLEKNMPIGSGLGSSACS

<h3>Task 3: Download Genomes from Uniprot</h3>

In [23]:
def getReadMe():
    
    #download the ReadMe from Uniprot
    os.system('wget ftp://ftp.uniprot.org/pub/databases/uniprot/current_release/knowledgebase/reference_proteomes/README')
    
    #open the README
    file = open('README','r+')
    
    #Read the file 
    contents = file.read()
    
    #Use regular expression to extract the proteome and taxonomic ids
    ids = re.findall(r'(UP[0-9]+)',contents)
    
    
    return ids

def downloadGenome(genome_id):
    
    #prepare the address
    address = 'ftp://ftp.uniprot.org/pub/databases/uniprot/current_release/knowledgebase/reference_proteomes/Bacteria/{}_*'.format(genome_id)
    
    #Download into a folder called Genomes
    os.system('wget -P Genomes/{} {}'.format(genome_id,address))

if __name__ == '__main__':
    
    #get the README
    ids = getReadMe()
    
    
    #select three genomes
    
    genomes = []
    
    genomes.append(ids[32])
    genomes.append(ids[9])
    genomes.append(ids[16])
    
    
    #Retrieve the genome for each of these
    for genome_id in genomes:
        
        downloadGenome(genome_id)
    
    

<h3>Task 4: Parse Uniprot Functional Annotations</h3>

In [14]:
def getAnnotations():
    
    #Download the file from Uniprot
    #os.system('wget ftp://ftp.uniprot.org/pub/databases/uniprot/current_release/knowledgebase/taxonomic_divisions/uniprot_sprot_archaea.dat.gz')
    
    #prepare a list of ids
    id_list = []
    
    #Open the file and parse
    with gzip.open('uniprot_sprot_archaea.dat.gz','r') as f:
        
        #Parse the file
        for seq_record in SeqIO.parse(f,'swiss'):
            
            #Extract the id(s)
            id = seq_record.annotations['ncbi_taxid']

            

            if id in id_list:
                
                pass
            
            else:
                
                id_list += id
                id = ','.join(id)
                organism = seq_record.annotations['organism']
                taxonomy = ','.join(seq_record.annotations['taxonomy'])
            
            
                print('{}\t{}\t{}'.format(id,organism,taxonomy))
            
            
if __name__ == '__main__':
    
    getAnnotations()
    

272844	Pyrococcus abyssi (strain GE5 / Orsay)	Archaea,Euryarchaeota,Thermococci,Thermococcales,Thermococcaceae,Pyrococcus
186497	Pyrococcus furiosus (strain ATCC 43587 / DSM 3638 / JCM 8422 / Vc1)	Archaea,Euryarchaeota,Thermococci,Thermococcales,Thermococcaceae,Pyrococcus
70601	Pyrococcus horikoshii (strain ATCC 700860 / DSM 12428 / JCM 9974 / NBRC 100139 / OT-3)	Archaea,Euryarchaeota,Thermococci,Thermococcales,Thermococcaceae,Pyrococcus
272557	Aeropyrum pernix (strain ATCC 700893 / DSM 11879 / JCM 9820 / NBRC 100138 / K1)	Archaea,Crenarchaeota,Thermoprotei,Desulfurococcales,Desulfurococcaceae,Aeropyrum
351160	Methanocella arvoryzae (strain DSM 22066 / NBRC 105507 / MRE50)	Archaea,Euryarchaeota,Methanomicrobia,Methanocellales,Methanocellaceae,Methanocella
368407	Methanoculleus marisnigri (strain ATCC 35101 / DSM 1498 / JR1)	Archaea,Euryarchaeota,Methanomicrobia,Methanomicrobiales,Methanomicrobiaceae,Methanoculleus
309800	Haloferax volcanii (strain ATCC 29605 / DSM 3757 / JCM 8879 / NBR